In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from random import randint
from collections import defaultdict
import re
import sys
import pickle
import random

from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import log_loss, mean_squared_error, r2_score, confusion_matrix
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import  RandomForestRegressor, AdaBoostRegressor, GradientBoostingRegressor
from sklearn.linear_model import LinearRegression
import tensorflow as tf
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation, LSTM
from tensorflow.keras.optimizers import SGD, RMSprop
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import LambdaCallback

import xgboost as xgb
from sklearn.feature_extraction import FeatureHasher
from sklearn.feature_extraction.text import HashingVectorizer, TfidfTransformer
from math import sqrt
import scipy.stats as stats
from scipy.stats import zscore

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

### Pull in all the data to make the lists that we will have the bot pick from.

In [ ]:
_2019 = pd.read_csv('../data/IMDB_mine_data_2019.csv',index_col=0)
_2018 = pd.read_csv('../data/IMDB_mine_data_2018.csv',index_col=0)
_2017 = pd.read_csv('../data/IMDB_mine_data_2017.csv',index_col=0)
_2016 = pd.read_csv('../data/IMDB_mine_data_2016.csv',index_col=0)
_2015 = pd.read_csv('../data/IMDB_mine_data_2015.csv',index_col=0)
#get all the films into one DF
films = pd.concat([_2019,_2018,_2017,_2016,_2015])
# remove the filler films we were using to start the mining bot
films = films[films['title_code'] != np.nan]
films = films[films['opening_wknd'] != np.nan]
films = films[films['release_date'] != '1980-05-16']
films.shape

In [ ]:
films.sample(1)

In [ ]:
all_actors = np.unique(films[['actor1', 'actor2','actor3','actor4','actor5','actor6','actor7','actor8', 'actor9','actor10']].dropna().values)
all_actors.shape

In [ ]:
all_actors = pd.Series(all_actors)
#all_actors.to_csv('../data/all_actors.csv')

In [ ]:
#clean the text in the production company column, and turn it into an accessable array
films['prod_co'] = films.prod_co.map(lambda x : re.findall(r"'(.*?)'",x, re.DOTALL))

#break production and distribution out into their own columns
films['production'] = films['prod_co'].map(lambda x : x[0] if len(x) >= 1 else np.nan)
films['production_2'] = films['prod_co'].map(lambda x : x[1] if len(x) >= 3 else np.nan)
films['distribution'] = films['prod_co'].map(lambda x : x[-1] if len(x) >= 2 else np.nan)

#convert the release date to a pandas datetime object
films['release_date'] = films['release_date'].map(lambda x : pd.to_datetime(x))

#Set the first director to their own column
films.directors = films.directors.map(lambda x : re.findall(r"'(.*?)'",x, re.DOTALL if isinstance(x, str) else np.nan))
films['director'] = films['directors'].map(lambda x: x[0] if len(x) >= 1 else 'none')

In [ ]:
directors = np.unique(films['director'].dropna().values)
directors = pd.Series(directors)
#directors.to_csv('../data/all_directors.csv')

In [ ]:
production = np.unique(films['production'].dropna().values)
production = pd.Series(production)
#production.to_csv('../data/all_production.csv')

In [ ]:
distribution = np.unique(films['distribution'].dropna().values)
distribution = pd.Series(distribution)
#distribution.to_csv('../data/all_distribution.csv')

In [ ]:
#Add the main producer and executive producer to the dataframe
producer_key = pd.read_csv('../data/producer_key.csv', index_col=0)
films = films.merge(producer_key, on='title_code', how='left')
#remove spaces in the names, and replace the fill values with empty strings
films['producer'] = films['producer'].map(lambda x : x if x!='[]' else None)
films['executive'] = films['executive'].map(lambda x : x if x!='[]' else None)

In [ ]:
producers = np.unique(films['producer'].dropna().values)
producers= pd.Series(producers)
#producers.to_csv('../data/all_producers.csv')

In [ ]:
executives = np.unique(films['executive'].dropna().values)
executives = pd.Series(executives)
#executives.to_csv('../data/all_executives.csv')

In [ ]:
budgets = np.unique(films['budget'].dropna().values)
budgets = pd.Series(budgets)
#budgets.to_csv('../data/all_budgets.csv')

# We have all the files exported to read into our "game"

In [ ]:
#import the lists to make our random picks from.
months = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 
         'November', 'December']
genre = ['action','adventure','animated','biography','drama','documentary','comedy','crime','fantasy','family',
         'musical','horror','war','mystery','sci-fi','thriller','romance']
rating = ['G', 'PG', 'PG-13', 'R', 'not-rated']

actors = pd.read_csv('../data/all_actors.csv', index_col=0)
directors = pd.read_csv('../data/all_directors.csv', index_col=0)
production = pd.read_csv('../data/all_production.csv', index_col=0)
distribution = pd.read_csv('../data/all_distribution.csv', index_col=0)
producers = pd.read_csv('../data/all_producers.csv', index_col=0)
executives = pd.read_csv('../data/all_executives.csv', index_col=0)
budgets = pd.read_csv('../data/all_budgets.csv', index_col=0)

In [ ]:
directors.sample(1).values[0,0] # We will just let pandas return us a random value from the series we've saved.

In [ ]:
actors['0'].sample(10).values.shape

actor10[0]

In [ ]:
actor10 = actors['0'].sample(10).values
director = directors.sample(1).values[0,0]
prod = production.sample(1).values[0,0]
dist = distribution.sample(1).values[0,0]
producer = producers.sample(1).values[0,0]
executive = executives.sample(1).values[0,0]
budget = budgets.sample(1).values[0,0]

film = pd.DataFrame(columns=['actor1', 'actor2', 'actor3', 'actor4', 'actor5', 'actor6', 'actor7', 'actor8', 'actor9',
                             'actor10', 'director', 'production', 'distribution', 'producer', 'executive', 'budget'])
film.loc[0] = [actor10[0], actor10[1], actor10[2], actor10[3], actor10[4], actor10[5], actor10[6]
               , actor10[7], actor10[8], actor10[9], director, prod, dist, producer, executive, budget]
film.head()

In [ ]:
# convert the actor codes to strings
actor_key = pd.read_csv('../data/actor_key.csv', index_col=0).reset_index()

def get_actor_name(key):
    #print(key)
    if isinstance(key, float):
        return key
    row = actor_key.loc[actor_key['actor'] == key].index[0]
    #print(type(actor_key.iloc[row]['name']), actor_key.iloc[row]['name'])
    return actor_key.iloc[row]['name']

def get_actor_key(name):
    #print(key)
    row = actor_key.loc[actor_key['name'] == name].index[0]
    return(actor_key.iloc[row]['actor'])

In [ ]:
film['actor_1'] = film['actor1'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_2'] = film['actor2'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_3'] = film['actor3'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_4'] = film['actor4'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_5'] = film['actor5'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_6'] = film['actor6'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_7'] = film['actor7'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_8'] = film['actor8'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_9'] = film['actor9'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)
film['actor_10'] = film['actor10'].map(lambda x : get_actor_name(x).replace(" ", '') if isinstance(x, str) else None)

film['actor_1_string'] = film['actor1'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_2_string'] = film['actor2'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_3_string'] = film['actor3'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_4_string'] = film['actor4'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_5_string'] = film['actor5'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_6_string'] = film['actor6'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_7_string'] = film['actor7'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_8_string'] = film['actor8'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_9_string'] = film['actor9'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)
film['actor_10_string'] = film['actor10'].map(lambda x : get_actor_name(x) if isinstance(x, str) else None)

In [ ]:
film.head()

In [ ]:
film['train_string'] = film[['production','distribution','director','actor_1','actor_2','actor_3','actor_4',
                               'actor_5','actor_6','actor_7','actor_8','actor_9','actor_10',
                               'producer','executive']].apply(lambda x: ' '.join(x.dropna().astype(str)), axis=1)

In [ ]:
film.head()

In [ ]:
rate = random.choice(rating)
genres = random.sample(genre,3)
month = random.choice(months)
print("you are making a "+ str(rate)+" rated film of the "+ ', '.join([str(x) for x in genres]) +" sort, that comes out in "+str(month))

film['rating'] = rate
film['genre'] = [genres]
film['release_month'] = month

In [ ]:
film.head()

In [ ]:
#we're going to do the OHE manually
film['action'] = film['genre'].map(lambda x : 1 if 'Action' in x else 0)
film['adventure']  = film['genre'].map(lambda x : 1 if 'Adventure' in x else 0)
film['animated'] = film['genre'].map(lambda x : 1 if 'Animation' in x else 0)
film['biography'] = film['genre'].map(lambda x : 1 if 'Biography' in x else 0)
film['drama'] = film['genre'].map(lambda x : 1 if 'Drama' in x else 0)
film['documentary'] = film['genre'].map(lambda x : 1 if 'Documentary' in x else 0)
film['comedy'] = film['genre'].map(lambda x : 1 if 'Comedy' in x else 0)
film['crime'] = film['genre'].map(lambda x : 1 if 'Crime' in x else 0)
film['fantasy'] = film['genre'].map(lambda x : 1 if 'Fantasy' in x else 0)
film['family'] = film['genre'].map(lambda x : 1 if 'Family' in x else 0)
film['musical'] = film['genre'].map(lambda x : 1 if 'Musical' in x else 0)
film['horror'] = film['genre'].map(lambda x : 1 if 'Horror' in x else 0)
film['war'] = film['genre'].map(lambda x : 1 if 'War' in x else 0)
film['mystery'] = film['genre'].map(lambda x : 1 if 'Mystery' in x else 0)
film['sci-fi'] = film['genre'].map(lambda x : 1 if 'Sci-Fi' in x else 0)
film['thriller'] = film['genre'].map(lambda x : 1 if 'Thriller' in x else 0)
film['romance'] = film['genre'].map(lambda x : 1 if 'Romance' in x else 0)

In [ ]:
#add actor popularity scores
fake_popularity = 10071118 #instantiated as the lowest actor popularity +1
def get_act_pop(code, fake_pop):
    if code in act_pop_keys['actor'].unique():
        row = act_pop_keys.loc[act_pop_keys['actor'] == code].index[0]
        return act_pop_keys.iloc[row]['popularity']
    else:
        return fake_pop + randint(0,1000)

act_pop_keys = pd.read_csv('../data/actor_popularity.csv', index_col=0)
act_pop_keys.reset_index(inplace=True, drop=True)

film['actor1_popularity'] = film['actor1'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor2_popularity'] = film['actor2'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor3_popularity'] = film['actor3'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor4_popularity'] = film['actor4'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor5_popularity'] = film['actor5'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor6_popularity'] = film['actor6'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor7_popularity'] = film['actor7'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor8_popularity'] = film['actor8'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor9_popularity'] = film['actor9'].map(lambda x : get_act_pop(x,fake_popularity))
film['actor10_popularity'] = film['actor10'].map(lambda x : get_act_pop(x,fake_popularity))

In [ ]:
def get_celeb_class(pop):
    if pop <=2000:
        return 'A-list'
    elif pop <= 5000:
        return 'B-list'
    elif pop <= 20000:
        return 'C-list'
    elif pop <= 100000:
        return 'D-list'
    elif pop <= 250000:
        return 'E-list'
    else:
        return 'nobody'
    
#convert popularity scores to text columns 
film['actor1_class'] = film['actor1_popularity'].map(lambda x : get_celeb_class(x))
film['actor2_class'] = film['actor2_popularity'].map(lambda x : get_celeb_class(x))
film['actor3_class'] = film['actor3_popularity'].map(lambda x : get_celeb_class(x))
film['actor4_class'] = film['actor4_popularity'].map(lambda x : get_celeb_class(x))
film['actor5_class'] = film['actor5_popularity'].map(lambda x : get_celeb_class(x))
film['actor6_class'] = film['actor6_popularity'].map(lambda x : get_celeb_class(x))
film['actor7_class'] = film['actor7_popularity'].map(lambda x : get_celeb_class(x))
film['actor8_class'] = film['actor8_popularity'].map(lambda x : get_celeb_class(x))
film['actor9_class'] = film['actor9_popularity'].map(lambda x : get_celeb_class(x))
film['actor10_class'] = film['actor10_popularity'].map(lambda x : get_celeb_class(x))

In [ ]:
dummy_blank = pd.read_csv('../data/dummy_blank.csv', index_col=0)
dummy_blank.head()

In [ ]:
dummy_blank.iloc[0, dummy_blank.columns.get_loc('release_month_'+film['release_month'][0]) ] = 1
dummy_blank.iloc[0, dummy_blank.columns.get_loc('actor1_class_'+film['actor1_class'][0]) ] = 1
dummy_blank.iloc[0, dummy_blank.columns.get_loc('actor2_class_'+film['actor2_class'][0]) ] = 1
dummy_blank.iloc[0, dummy_blank.columns.get_loc('actor3_class_'+film['actor3_class'][0]) ] = 1
if film['rating'][0] == 'not-rated':
    dummy_blank.iloc[0, dummy_blank.columns.get_loc('rating_'+'Not Rated') ] = 1
else:
    dummy_blank.iloc[0, dummy_blank.columns.get_loc('rating_'+film['rating'][0]) ] = 1
dummy_blank.head()

In [ ]:
vectorizer = HashingVectorizer(n_features=1000)
vector = vectorizer.fit_transform(film['train_string'].to_numpy())
vec_df = pd.DataFrame.sparse.from_spmatrix(vector)

In [ ]:
use_cols = film[['budget','action','adventure','animated','biography','drama','documentary','comedy','crime',
                        'fantasy','family','musical','horror','war','mystery','sci-fi','thriller','romance']]

In [ ]:
X = pd.concat([use_cols, dummy_blank, vec_df], axis=1, sort=False)
X.head()

In [ ]:
model_gb = pickle.load(open('../data/gb_model.pkl', 'rb'))
prediction = model_gb.predict(X)
print(prediction)

In [ ]:
film.genre[0]

# Here I'm beginning to train an LSTM nn to produce titles for us
first thing I need to do is grab all the titles I can get and load them into a single block of raw text to train on.

In [3]:
#these are just tiles from my data-set
_2019 = pd.read_csv('../data/IMDB_mine_data_2019-oversample.csv',index_col=0)
_2018 = pd.read_csv('../data/IMDB_mine_data_2018-oversample.csv',index_col=0)
_2017 = pd.read_csv('../data/IMDB_mine_data_2017.csv',index_col=0)
_2016 = pd.read_csv('../data/IMDB_mine_data_2016.csv',index_col=0)
_2015 = pd.read_csv('../data/IMDB_mine_data_2015.csv',index_col=0)
_2014 = pd.read_csv('../data/IMDB_mine_data_2014.csv',index_col=0)
#get all the films into one DF
films = pd.concat([_2019,_2018,_2017,_2016,_2015,_2014])
string = ' | '.join(films['title'].to_numpy())
string

'Home Movies | The Fetishist | Travel Daze | Danger Close | The Dirt | Cine Manifest | Bolden | Fiddler: A Miracle of Miracles | Soccer in the City | Paradise | In Their Own Words, Billy the Kid & The Lincoln County War | A Christmas Prince: The Royal Baby | He\'s My Daddy Too | On the Trail of Bigfoot | Terror in the Skies | Bull | Troublemaker | Snatchers | Willie | Family Obligations | Encrypted: The Cyber Crime | Bigger Like Me (Extended Director\'s Cut) | Mossville: When Great Trees Fall | 17 Blocks | My Neighbor Wants Me Dead | Watson | Nomad: In the Footsteps of Bruce Chatwin | Picture Character | Changing the Game | The Soul of Soho | Lucky Grandma | Martha: A Picture Story | You Don\'t Nomi | Linda Ronstadt: The Sound of My Voice | The Remix: Hip Hop X Fashion | Slay the Dragon | Trixie Mattel: Moving Parts | Iris: A Space Opera by Justice | Out and About Movie 2: Las Vegas Adventure | RC Propbusters: Untold | The Deed | Ancestral Waters | 919 Lakeview Drive | Ispade Rajavum I

In [65]:
#these are ALL of the english film titles on IMDB
all_titles = pd.read_csv('https://galvbucket.s3-us-west-1.amazonaws.com/titles_for_text_training.csv')
string = '  |  '.join(all_titles.title.to_numpy())
string

'The Arrival of a Train  |  The Arrival of a Train at La Ciotat  |  The Arrival of a Train  |  Boat Leaving the Port  |  Baby\'s Meal  |  Arrival of a Train at Vincennes Station  |  The Sprinkler Sprinkled  |  Leaving Jerusalem by Railway  |  The Devil\'s Castle  |  Workers Exit from the Confianca Shirt Factory  |  A Terrible Night  |  Card Party  |  Bathing in a Stream  |  The Burglars  |  At the Hypnotist\'s  |  A Badly Managed Hotel  |  The Cabinet of Mephistopheles  |  Niagara Falls  |  The Niagara Waterfall  |  The Fisherman at the Stream  |  The Exhibition Sausage Seller and the Billposter  |  A Trip to the Moon  |  The Moon at One Meter  |  The Moon at Arm\'s Length  |  Disappearing Act  |  At the Club  |  Portuguese Railway Train  |  The Pillar of Fire  |  Army Life; or, How Soldiers Are Made: Mounted Infantry  |  Army Life; or, How Soldiers Are Made: Mounted Infantry  |  Pierrette\'s Escapades  |  Maple Viewing  |  Maple Leaf Viewing  |  The India Rubber Head  |  A Road for Ch

In [4]:
processed_text = string.lower()
processed_text = re.sub(r'[^\x00-\x7f]',r'', processed_text)
processed_text

'home movies | the fetishist | travel daze | danger close | the dirt | cine manifest | bolden | fiddler: a miracle of miracles | soccer in the city | paradise | in their own words, billy the kid & the lincoln county war | a christmas prince: the royal baby | he\'s my daddy too | on the trail of bigfoot | terror in the skies | bull | troublemaker | snatchers | willie | family obligations | encrypted: the cyber crime | bigger like me (extended director\'s cut) | mossville: when great trees fall | 17 blocks | my neighbor wants me dead | watson | nomad: in the footsteps of bruce chatwin | picture character | changing the game | the soul of soho | lucky grandma | martha: a picture story | you don\'t nomi | linda ronstadt: the sound of my voice | the remix: hip hop x fashion | slay the dragon | trixie mattel: moving parts | iris: a space opera by justice | out and about movie 2: las vegas adventure | rc propbusters: untold | the deed | ancestral waters | 919 lakeview drive | ispade rajavum i

In [5]:
print('corpus length:', len(processed_text))

chars = sorted(list(set(processed_text)))
print('total chars:', len(chars))
char_indices = dict((c, i) for i, c in enumerate(chars))
indices_char = dict((i, c) for i, c in enumerate(chars))

corpus length: 307905
total chars: 64


In [6]:
# cut the text in semi-redundant sequences of maxlen characters
maxlen = 40
step = 3
sentences = []
next_chars = []
for i in range(0, len(processed_text) - maxlen, step):
    sentences.append(processed_text[i: i + maxlen])
    next_chars.append(processed_text[i + maxlen])
print('nb sequences:', len(sentences))

nb sequences: 102622


In [7]:
sentences

['home movies | the fetishist | travel daz',
 'e movies | the fetishist | travel daze |',
 'ovies | the fetishist | travel daze | da',
 'es | the fetishist | travel daze | dange',
 '| the fetishist | travel daze | danger c',
 'he fetishist | travel daze | danger clos',
 'fetishist | travel daze | danger close |',
 'ishist | travel daze | danger close | th',
 'ist | travel daze | danger close | the d',
 ' | travel daze | danger close | the dirt',
 'travel daze | danger close | the dirt | ',
 'vel daze | danger close | the dirt | cin',
 ' daze | danger close | the dirt | cine m',
 'ze | danger close | the dirt | cine mani',
 '| danger close | the dirt | cine manifes',
 'anger close | the dirt | cine manifest |',
 'er close | the dirt | cine manifest | bo',
 'close | the dirt | cine manifest | bolde',
 'se | the dirt | cine manifest | bolden |',
 '| the dirt | cine manifest | bolden | fi',
 'he dirt | cine manifest | bolden | fiddl',
 'dirt | cine manifest | bolden | fiddler:',
 't | cine

In [8]:
print('Vectorization...')
x = np.zeros((len(sentences), maxlen, len(chars)), dtype=np.bool)
y = np.zeros((len(sentences), len(chars)), dtype=np.bool)
for i, sentence in enumerate(sentences):
    for t, char in enumerate(sentence):
        x[i, t, char_indices[char]] = 1
    y[i, char_indices[next_chars[i]]] = 1

Vectorization...


In [9]:
# build the model: a single LSTM
print('Build model...')
model = Sequential()
model.add(LSTM(128, input_shape=(maxlen, len(chars))))
model.add(Dense(len(chars), activation='softmax'))

optimizer = RMSprop(lr=0.01)
model.compile(loss='categorical_crossentropy', optimizer=optimizer)

Build model...


In [37]:
print('load model...')
model = keras.models.load_model('../data/title_generator_local')

load model...


In [11]:
def sample(preds, temperature=1.0):
    # helper function to sample an index from a probability array
    preds = np.asarray(preds).astype('float64')
    preds = np.log(preds) / temperature
    exp_preds = np.exp(preds)
    preds = exp_preds / np.sum(exp_preds)
    probas = np.random.multinomial(1, preds, 1)
    return np.argmax(probas)

In [38]:

def on_epoch_end(epoch, _):
    # Function invoked at end of each epoch. Prints generated text.
    print("****************************************************************************")
    print('----- Generating text after Epoch: %d' % epoch)
    
    if epoch %2 == 0 and epoch > 1:
        start_index = random.randint(0, len(processed_text) - maxlen - 1)
        for temperature in [ 1.0]:
            print('----- temperature:', temperature)

            generated = ''
            sentence = processed_text[start_index: start_index + maxlen]
            generated += sentence
            print('----- Generating with seed: "' + sentence + '"')
            sys.stdout.write(generated)

            for i in range(1200):
                x_pred = np.zeros((1, maxlen, len(chars)))
                for t, char in enumerate(sentence):
                    x_pred[0, t, char_indices[char]] = 1.

                preds = model.predict(x_pred, verbose=0)[0]
                next_index = sample(preds, temperature)
                next_char = indices_char[next_index]

                generated += next_char
                sentence = sentence[1:] + next_char

                sys.stdout.write(next_char)
                sys.stdout.flush()
            with open('../data/raw_generated_text_local.txt', "a+") as f:
                  f.write(generated[maxlen:]+"\n")
            print()
    else:
        pass

In [ ]:
import logging, os
logging.disable(logging.WARNING)
os.environ["TF_CPP_MIN_LOG_LEVEL"] = "3"

# Fit the model
print_callback = LambdaCallback(on_epoch_end=on_epoch_end)

model.fit(x, y,
          batch_size=128,
          epochs=6,
          callbacks=[print_callback])

Train on 102622 samples
Epoch 1/6
102528/102622 [============================>.] - ETA: 0s - loss: 1.3426****************************************************************************
----- Generating text after Epoch: 0
102622/102622 [==============================] - 206s 2ms/sample - loss: 1.3426
Epoch 2/6
 54400/102622 [==============>...............] - ETA: 1:32 - loss: 1.3033

In [50]:
#model = pickle.load(open('../data/text_gen_model.pkl', "rb"))
model.save('../data/title_generator_local')

In [30]:
def spit_out_text():
    # Function invoked at end of each epoch. Prints generated text.
    print("****************************************************************************")
    #print('----- Generating text after Epoch: %d' % epoch)
    
    start_index = random.randint(0, len(processed_text) - maxlen - 1)
    for temperature in [ 1.0]:
        print('----- temperature:', temperature)

        generated = ''
        sentence = processed_text[start_index: start_index + maxlen]
        #sentence = 'the matrix  |  the fifth element  |  han'
        generated += sentence
        print('----- Generating with seed: "' + sentence + '"')
        sys.stdout.write(generated)

        for i in range(1000):
            x_pred = np.zeros((1, maxlen, len(chars)))
            for t, char in enumerate(sentence):
                x_pred[0, t, char_indices[char]] = 1.

            preds = model.predict(x_pred, verbose=0)[0]
            next_index = sample(preds, temperature)
            next_char = indices_char[next_index]

            generated += next_char
            sentence = sentence[1:] + next_char

            sys.stdout.write(next_char)
            sys.stdout.flush()
        with open('../data/raw_generated_text_local.txt', "a+") as f:
              f.write(generated[maxlen:]+"\n")
        print()


In [33]:
for _ in range(100):
    spit_out_text()

****************************************************************************
----- temperature: 1.0
----- Generating with seed: "i | the huntress: rune of the dead | awa"
i | the huntress: rune of the dead | awarken leaves | out torkey | street devolings | chapper grave | legend of got | beyond the mo: inside house of the nance and worl | christmas grind | sechold: being lana camera | ratgers of a remember

/Users/owenmorris/anaconda/lib/python3.6/site-packages/ipykernel_launcher.py:4: RuntimeWarning: divide by zero encountered in log
  after removing the cwd from sys.path.


s | mn mountain to nurre | quiet suide pillence | femingt club | searly unskeet shawler | american gocky | myn bukin a standilis | bond of justiue | sah via more | in the diven ugond | naluvar | the blood factory | the invalomation | miss beautiful the potewh| journey women | take deofnlea | mrlek sice | next deaint | hell's spret | silence | seofilis | minnistical or of heartle in spin | the hail werst wilder night rimben | the roady | deadly | the stoned drop | superstory | fakpany | busing shadows | jusis in priest: robert greelotal american matter | alien son turning | quin trature | do not in vieble | show the american kirth | in turn | as youl love everyn children's the story of the good: hail | sleef dues | my personac thoopito | open stairior | piscampaniese: the 2-geve, what part 2 
****************************************************************************
----- temperature: 1.0
----- Generating with seed: " | down's revenge | i had a dream | ques"
 | down's revenge | i had 

is brown: welcome to my life | the beguing wis | the making me | assassin and crognganver to trop | the nelvever house: a possit porsulors | poanher shadows | fares allema | light | bet: the story of juctorious of bayraghabiration | ney god novady | atsass of the bi | kill | death | the brotherlavar broak | expedil like street: the peramenwand | the centernous | in love and the fire | ballitters of johnny history of an eleased phrists | humation of america | goodgyouse | tiny. ne- your uped castrocy craugesvag, mame frience fearne | rainy fairver | annible of mark | biyfiel you love girh | taskessional world every. on goes | the wintordie | raderor, no sere | wulster | grindme fifter | exbers days | friends acofest | monster to deore dragon | omp | goord the last stories | alien double ngali 2 | the story of dawn | dpups grannic the would | deadly seven | sunkinness | all they murderse days | freak hero | me piece: part gyzam metalistic | husting for beg | salmotaror | the moon | kill 

| chips | rings | krystal | justice leag!! | they un | the mostiles fridhol | sicilly project story | attaider | arteul story planetfall | first mar | when the spin | footate movie | the missings is love | zoeby | zero: my lost | bare, and pavetuel | show huge fire | viosem: hellletican ground | indneller are story - samah | silencess boy | of montimes 2 story: doon ats | marad waol wan new memstrigl | ir100 of afrach | the greenpmance | the sait kille fly: the devil's red pinter | crauman | savixer | paration massanda | game at two for eist to glow|illess | the proglest | de3rly the american jip plarle | girlfaeth dark | far 2 galu: a 'lets | my friend of the force to the de, grass | kadaek and the stage: misiaren ground | the presentsiic's inside | 24 day modussidector | bewter in a beest | roads birth | opi boingous | silent of the bast | the luby! | the social presents: blackter does at wispless | like the kids | love sking | day to spylward arried free | handy reall uncimillers | 

...

race | el da de la unin | upstate story | up walke 2 | stout wild tomouth race arcus funcine, pree garway | monster where | califorting yourcool the best ratty realwond bloodkyddics | taks of die | biwq grinded | medied | auto the smakeswurraz mecownerch | fort villem - persincity | something show | goody what adren marad | brothernight gangst | america | buline | the goldingeming | titituors | side of savie | vavaghouse | in love the light |  stories to skyrys | marruil | flayamma | sa...a. te - holiday grick | the dark fight 20y | american kings | restores minu | sheeking the baset | history of star | old yours to dotglood | house, stalk in bagzks, and beusion - me from hatch | girlfartad | manuversavamharations | paranormal | by the our death | devil's untrosham | wilding collision: lonerland: intersess of bak: the more hauds mersgocion | bot searthing this 1 | blood everyd dance | sleanner pousting | does brother | porn0prou | mill & jru sgoveracos | in taie grave paout | accs odzi

eiss: the beat goddess | celebrity crush | you gned grandmohalo-shose | finding all for rog nation | krays and suffetroidgo sthollight school laku | years of hero | the trutching brakx | mulle | bell: johnson alies trainch fox | there widd road | up awaily | fun mariah | jlusic anname after we lavarme | timeland | bet: the dark man | the gnoel&y, the flay | cwbacha | bitperpleds | the movie | smaking passion | walks the holloween the lose | disasivendy fourd: collissing the restoran | inside poidc to cappionation | renuprohit | 5bthers girls in the hers: a smeeteng world cloue | cop of the dark | orouvale switchines | airan | nary annicanteup | gladhof vacks winr | ecewas meet | return not cootranchangers | my all ywiengss | the girls and with fall | femil life | toglo | sally | boid & ro, grave easheil | aniyed music: america wind: the family | | the thsmarcobots: the last triol seein | clownsperon's amenger | miracle and the lies to dies the devil securture | bold gunouy fortal | the

nes: the sculpture of robert wiggs | bumbleappres livist | selly la bersying alone | wakengjy | dence | the life at the devil friends | marcy | unknown kirs | royal mows em4 | nuzer | my most in the theatres at all tale | vicon | bale on ementer | screw no art | malicing ere : the hobil contem | wordsmiir! | sele's histor my gial | los arberdard | brerks | merlald bendard | rock and the apolo | beauty and cally distoring 2: rob all thool | breaking of of the last marvinez | text is sos in the fyller | fate: a haudly's wasstuning brain an experes | the life at requi bet scatt | melturgiague | selvia | sofighe an mankin | far | renotian | good: the el and neare collise | american lilndrevon | crompable house | southman coright | harvest of immitorion: dombitate pilled | ii speakn-ridess | kip know new yerbar | laughter | kaitmi | 20 cablechets | the droplance of secrets | crows | dian dreams | dparrorh the never | my night | lovelaples | palace | nafith dibome: the: valvioogians | journe

 | cruel hearts | soul to keep | cruise | crossing of the exblate: my not chanrow | crime bug | nock with requii | no hade gabacebbectors: the grand meure of molly | christsac sat every woryf cogloue | fragh tapedar | rose the sast pivents | sebeng is to setji | choco man | the cirl | the traugh: a name christman | party | the secrut banceup | telsine changale | turned zoe | the extrain | everything fare at all and drke-school | munder | the swinghe looking 2019 | presentsiale gianda | clounp 20199 fell ammer | rrol hosting 14 - onighect | the the ursean how the laughter | acts is joes | century bire | kratcy for mr. rain | ring aidents | wastmor | light isidis never : christmas is love | tel attair | ravering three | once at the times | story kinger | demongr | isllegger | wild weld: the tobbot..anhorriess of br: uslande capin life | silicoxt rcacion | the penicic | unvoyayaration | tarma of ta-kecb | laughter | are litter wilderstes of sarar | the glinued | the tires of wilfridess | 

KeyboardInterrupt: 

In [35]:
generated = 'thisidfasdf;lj;lkajsdfl;kajsdf;lkajsdf;lajsdfl;aksjdf;alskjdf'
generated[20:]

'dfl;kajsdf;lkajsdf;lajsdfl;aksjdf;alskjdf'